# LSTM-arithmetic

## Dataset
- [Arithmetic dataset](https://drive.google.com/file/d/1cMuL3hF9jefka9RyF4gEBIGGeFGZYHE-/view?usp=sharing)

In [116]:
# ! pip install seaborn
# ! pip install opencc
# ! pip install -U scikit-learn

import numpy as np
import pandas as pd
import torch
import torch.nn
import torch.nn.utils.rnn
import torch.utils.data
import matplotlib.pyplot as plt
import seaborn as sns
import opencc
import os
from sklearn.model_selection import train_test_split

data_path = './data'

In [117]:
df_train = pd.read_csv(os.path.join(data_path, 'arithmetic_train.csv'))
df_eval = pd.read_csv(os.path.join(data_path, 'arithmetic_eval.csv'))
df_train.head()

Unnamed: 0          src   tgt
0     2285313  14*(43+20)=   882
1      317061     (6+1)*5=    35
2      718770    13+32+29=    74
3      170195   31*(3-11)=  -248
4     2581417     24*49+1=  1177

In [118]:
# transform the input data to string
df_train['tgt'] = df_train['tgt'].apply(lambda x: str(x))
df_train['src'] = df_train['src'].add(df_train['tgt'])
df_train['len'] = df_train['src'].apply(lambda x: len(x))

df_eval['tgt'] = df_eval['tgt'].apply(lambda x: str(x))
df_eval['src'] = df_eval['src'].add(df_eval['tgt'])
df_eval['len'] = df_eval['src'].apply(lambda x: len(x))

# Build Dictionary
 - The model cannot perform calculations directly with plain text.
 - Convert all text (numbers/symbols) into numerical representations.
 - Special tokens
    - '&lt;pad&gt;'
        - Each sentence within a batch may have different lengths.
        - The length is padded with '&lt;pad&gt;' to match the longest sentence in the batch.
    - '&lt;eos&gt;'
        - Specifies the end of the generated sequence.
        - Without '&lt;eos&gt;', the model will not know when to stop generating.

In [119]:
char_to_id = {}
id_to_char = {}

# write your code here
# Build a dictionary and give every token in the train dataset an id
# The dictionary should contain <eos> and <pad>
# char_to_id is to conver charactors to ids, while id_to_char is the opposite
pairs = [(0, '<pad>'), (1, '<eos>'), (2, '0'), (3, '1'), (4, '2'), (5, '3'), (6, '4'), (7, '5'), \
         (8, '6'), (9, '7'), (10, '8'), (11, '9'), (12, '+'), (13, '-'), (14, '*'), (15, '/'), \
         (16, '('), (17, ')'), (18, '=')]

for p in pairs:
    char_to_id[p[1]] = p[0]
    id_to_char[p[0]] = p[1]

vocab_size = len(char_to_id)
print('Vocab size = {}'.format(vocab_size))

Vocab size = 19


# Data Preprocessing
 - The data is processed into the format required for the model's input and output.
 - Example: 1+2-3=0
     - Model input: 1 + 2 - 3 = 0
     - Model output: / / / / / 0 &lt;eos&gt;  (the '/' can be replaced with &lt;pad&gt;)
     - The key for the model's output is that the model does not need to predict the next character of the previous part. What matters is that once the model sees '=', it should start generating the answer, which is '0'. After generating the answer, it should also generate&lt;eos&gt;


In [120]:
# Write your code here
def data_preprocessing(data):
    df_train.head()
    char_id_list = []
    label_id_list = []

    for i in range(len(data)):
        temp1 = []
        temp2 = []
        ans = False
        for c in data.iloc[i, 1]:
            temp1.append(char_to_id[c])
            
            if not ans:
                temp2.append(char_to_id['<pad>'])
            else:
                temp2.append(char_to_id[c])
            
            if c == '=':
                ans = True
        temp1.append(char_to_id['<eos>'])
        temp2.append(char_to_id['<eos>'])
        char_id_list.append(temp1)
        label_id_list.append(temp2)
        
    return (char_id_list, label_id_list)

L = data_preprocessing(df_train)
df_train['char_id_list'] = L[0]
df_train['label_id_list'] = L[1]

M = data_preprocessing(df_eval)
df_eval['char_id_list'] = M[0]
df_eval['label_id_list'] = M[1]

df_train.head()


Unnamed: 0             src   tgt  len  \
0     2285313  14*(43+20)=882   882   14   
1      317061      (6+1)*5=35    35   10   
2      718770     13+32+29=74    74   11   
3      170195  31*(3-11)=-248  -248   14   
4     2581417    24*49+1=1177  1177   12   

                                        char_id_list  \
0  [3, 6, 14, 16, 6, 5, 12, 4, 2, 17, 18, 10, 10,...   
1             [16, 8, 12, 3, 17, 14, 7, 18, 5, 7, 1]   
2           [3, 5, 12, 5, 4, 12, 4, 11, 18, 9, 6, 1]   
3  [5, 3, 14, 16, 5, 13, 3, 3, 17, 18, 13, 4, 6, ...   
4        [4, 6, 14, 6, 11, 12, 3, 18, 3, 3, 9, 9, 1]   

                                     label_id_list  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 4, 1]  
1                [0, 0, 0, 0, 0, 0, 0, 0, 5, 7, 1]  
2             [0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 6, 1]  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 13, 4, 6, 10, 1]  
4          [0, 0, 0, 0, 0, 0, 0, 0, 3, 3, 9, 9, 1]

# Hyper Parameters

|Hyperparameter|Meaning|Value|
|-|-|-|
|`batch_size`|Number of data samples in a single batch|64|
|`epochs`|Total number of epochs to train|10|
|`embed_dim`|Dimension of the word embeddings|256|
|`hidden_dim`|Dimension of the hidden state in each timestep of the LSTM|256|
|`lr`|Learning Rate|0.001|
|`grad_clip`|To prevent gradient explosion in RNNs, restrict the gradient range|1|

In [121]:
batch_size = 64
epochs = 1
embed_dim = 16
hidden_dim = 256
lr = 0.001
grad_clip = 1

# Data Batching
- Use `torch.utils.data.Dataset` to create a data generation tool called  `dataset`.
- The, use `torch.utils.data.DataLoader` to randomly sample from the `dataset` and group the samples into batches.

In [122]:
class Dataset(torch.utils.data.Dataset):
    def __init__(self, sequences):
        self.sequences = sequences
    
    def __len__(self):
        # return the amount of data
        return len(self.sequences)
    
    def __getitem__(self, index):
        # Extract the input data x and the ground truth y from the data
        x = self.sequences['char_id_list'][index] # Write your code here
        y = self.sequences['label_id_list'][index] # Write your code here
        return x, y

# collate function, used to build dataloader
def collate_fn(batch):
    batch_x = [torch.tensor(data[0]) for data in batch]
    batch_y = [torch.tensor(data[1]) for data in batch]
    batch_x_lens = torch.LongTensor([len(x) for x in batch_x])
    batch_y_lens = torch.LongTensor([len(y) for y in batch_y])
    
    # Pad the input sequence
    pad_batch_x = torch.nn.utils.rnn.pad_sequence(batch_x,
                                                  batch_first=True,
                                                  padding_value=char_to_id['<pad>'])
    
    pad_batch_y = torch.nn.utils.rnn.pad_sequence(batch_y,
                                                  batch_first=True,
                                                  padding_value=char_to_id['<pad>'])
    
    return pad_batch_x, pad_batch_y, batch_x_lens, batch_y_lens

In [123]:
ds_train = Dataset(df_train[['char_id_list', 'label_id_list']])
ds_eval = Dataset(df_eval[['char_id_list', 'label_id_list']])
ds_train[0]

([3, 6, 14, 16, 6, 5, 12, 4, 2, 17, 18, 10, 10, 4, 1],
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 4, 1])

In [124]:
# Build dataloader of train set and eval set, collate_fn is the collate function
dl_train = torch.utils.data.DataLoader(ds_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn)
dl_eval = torch.utils.data.DataLoader(ds_eval, batch_size=batch_size, shuffle=True, collate_fn=collate_fn)

# Model Design

## Execution Flow
1. Convert all characters in the sentence into embeddings.
2. Pass the embeddings through an LSTM sequentially.
3. The output of the LSTM is passed into another LSTM, and additional layers can be added.
4. The output from all time steps of the final LSTM is passed through a Fully Connected layer.
5. The character corresponding to the maximum value across all output dimensions is selected as the next character.

## Loss Function
Since this is a classification task, Cross Entropy is used as the loss function.

## Gradient Update
Adam algorithm is used for gradient updates.

In [125]:
class CharRNN(torch.nn.Module):
    def __init__(self, vocab_size, embed_dim, hidden_dim):
        super(CharRNN, self).__init__()
        
        self.embedding = torch.nn.Embedding(num_embeddings=vocab_size,
                                            embedding_dim=embed_dim,
                                            padding_idx=char_to_id['<pad>'])
        
        self.rnn_layer1 = torch.nn.LSTM(input_size=embed_dim,
                                        hidden_size=hidden_dim,
                                        batch_first=True)
        
        self.rnn_layer2 = torch.nn.LSTM(input_size=hidden_dim,
                                        hidden_size=hidden_dim,
                                        batch_first=True)
        
        self.linear = torch.nn.Sequential(torch.nn.Linear(in_features=hidden_dim,
                                                          out_features=hidden_dim),
                                          torch.nn.ReLU(),
                                          torch.nn.Linear(in_features=hidden_dim,
                                                          out_features=vocab_size))
        
    def forward(self, batch_x, batch_x_lens):
        return self.encoder(batch_x, batch_x_lens)
    
    # The forward pass of the model
    def encoder(self, batch_x, batch_x_lens):
        batch_x = self.embedding(batch_x)
        
        batch_x = torch.nn.utils.rnn.pack_padded_sequence(batch_x,
                                                          batch_x_lens,
                                                          batch_first=True,
                                                          enforce_sorted=False)
        
        batch_x, _ = self.rnn_layer1(batch_x)
        batch_x, _ = self.rnn_layer2(batch_x)
        
        batch_x, _ = torch.nn.utils.rnn.pad_packed_sequence(batch_x,
                                                            batch_first=True)
        
        batch_x = self.linear(batch_x)
        
        return batch_x
    
    def generator(self, start_char, max_len=200):
        
        char_list = [char_to_id[c] for c in start_char]
        
        next_char = None
        
        while len(char_list) < max_len: 
            # Write your code here 
            # Pack the char_list to tensor
            x = torch.LongTensor(char_list).unsqueeze(0)
            # Input the tensor to the embedding layer, LSTM layers, linear respectively
            x = self.embedding(x)
            # print(f'x = {x}')
            _, (ht, _) = self.rnn_layer1(x)
            _, (ht, _) = self.rnn_layer2(ht)
            y = self.linear(ht) # Obtain the next token prediction y
            # print(f'y = {y}')
            
            next_char = torch.argmax(y, num=-1) # Use argmax function to get the next token prediction
            
            if next_char == char_to_id['<eos>']:
                break
            
            char_list.append(next_char)
            
        return [id_to_char[ch_id] for ch_id in char_list]

In [126]:
torch.manual_seed(2)

device = torch.device("cuda:0") if torch.cuda.is_available() else torch.device("mps") if torch.backends.mps.is_available() else torch.device("cpu")


model = CharRNN(vocab_size,
                embed_dim,
                hidden_dim)

In [127]:
criterion = torch.nn.CrossEntropyLoss(ignore_index=char_to_id['<pad>'], reduction='mean') # Write your code here. Cross-entropy loss function. The loss function should ignore <pad>
optimizer = optimizer = torch.optim.AdamW(model.parameters(), lr=lr) # Write your code here. Use Adam or AdamW for Optimizer

# Training
1. The outer `for` loop controls the `epoch`
    1. The inner `for` loop uses `data_loader` to retrieve batches.
        1. Pass the batch to the `model` for training.
        2. Compare the predicted results `batch_pred_y` with the true labels `batch_y` using Cross Entropy to calculate the loss `loss`
        3. Use `loss.backward` to automatically compute the gradients.
        4. Use `torch.nn.utils.clip_grad_value_` to limit the gradient values between `-grad_clip` &lt; and &lt; `grad_clip`.
        5. Use `optimizer.step()` to update the model (backpropagation).
2.  After every `1000` batches, output the current loss to monitor whether it is converging.

In [128]:
from tqdm import tqdm
from copy import deepcopy
model = model.to(device)
model.train()
i = 0
flag = False
for epoch in range(1, epochs+1):
    # The process bar
    bar = tqdm(dl_train, desc=f"Train epoch {epoch}")
    for batch_x, batch_y, batch_x_lens, batch_y_lens in bar:
        if not flag:
            flag = True
            print(batch_x)
            print(batch_y)
            print(batch_x_lens)
            print(batch_y_lens)
        # Write your code here
        # Clear the gradient
        optimizer.zero_grad()
        batch_pred_y = model(batch_x.to(device), batch_x_lens)
        
        # Write your code here
        # Input the prediction and ground truths to loss function
        # print(f'batch_pred_y = {batch_pred_y}')
        # print(f'batch_y = {batch_y}')
        loss = criterion(batch_pred_y.view(-1, vocab_size), batch_y.view(-1).to(device))
        # Back propagatio.
        loss.backward()
        torch.nn.utils.clip_grad_value_(model.parameters(), grad_clip) # gradient clipping

        # Write your code here
        # Optimize parameters in the model
        optimizer.step()
        i+=1
        if i%50==0:
            bar.set_postfix(loss = loss.item())
    
    # Evaluate your model
    bar = tqdm(dl_eval, desc=f"Validation epoch {epoch}")
    matched = 0
    total = 0
    for batch_x, batch_y, batch_x_lens, batch_y_lens in bar:
        
        predictions = model(batch_x.to(device), batch_x_lens) # Write your code here. Input the batch_x to the model and generate the predictions
        
        predicted_tokens = torch.argmax(predictions, dim=-1) # (batch_size, seq_len)
        # Write your code here.
        # Check whether the prediction match the ground truths
        print(f'prdicted_tokens = {predicted_tokens}')
        print(f'batch_y = {batch_y}')
        print(f'batch_y_lens = {batch_y_lens}')
        # for pred, truth, length in zip(predicted_tokens, batch_y, batch_y_lens):
        #     pred, truth = pred[:length].cpu(), truth[:length].cpu()  # Trim to sequence length
        #     if torch.equal(pred, truth):  # Exact match comparison
        #         matched += 1
        #     total += 1
        # Compute exact match (EM) on the eval dataset
        # EM = correct/total

        
    # print(matched/total)

Train epoch 1:   0%|          | 24/37020 [00:00<04:59, 123.39it/s]

tensor([[ 4, 10, 14,  ...,  0,  0,  0],
        [ 3, 10, 14,  ...,  0,  0,  0],
        [ 8, 13,  4,  ...,  0,  0,  0],
        ...,
        [ 3, 11, 12,  ...,  0,  0,  0],
        [ 6,  8, 13,  ...,  0,  0,  0],
        [ 6,  7, 13,  ...,  2,  1,  0]])
tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 2, 1, 0]])
tensor([13, 13, 13, 14, 10, 14, 13, 17, 14, 12, 13, 13, 13, 13, 13, 16, 11, 16,
        13, 12, 15, 11, 13, 12, 15, 13, 12, 14, 15, 13, 12, 14, 16, 13, 10, 12,
        16, 12, 15, 14, 15, 14, 14, 12, 13, 14, 13, 12, 13, 13, 14, 14, 14, 15,
        12, 12, 13, 12, 14, 12, 12, 12, 12, 16])
tensor([13, 13, 13, 14, 10, 14, 13, 17, 14, 12, 13, 13, 13, 13, 13, 16, 11, 16,
        13, 12, 15, 11, 13, 12, 15, 13, 12, 14, 15, 13, 12, 14, 16, 13, 10, 12,
        16, 12, 15, 14, 15, 14, 14, 12, 13, 14, 13, 12, 13, 13, 14, 14, 14, 15,

Validation epoch 1:   1%|          | 51/4114 [00:00<00:16, 251.20it/s]

prdicted_tokens = tensor([[ 8,  2, 10,  ..., 11, 11, 11],
        [ 9,  8,  9,  ...,  8,  1, 11],
        [ 4,  2,  5,  ..., 11, 11, 11],
        ...,
        [ 8,  4,  7,  ...,  6,  1, 11],
        [ 3, 11, 13,  ...,  1, 11, 11],
        [ 3,  2,  6,  ..., 11, 11, 11]], device='cuda:0')
batch_y = tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 8, 1, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 6, 1, 0],
        [0, 0, 0,  ..., 1, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0]])
batch_y_lens = tensor([14, 16, 12, 16, 15, 11, 12, 11, 12, 16, 11, 12, 15, 14, 14, 13, 15, 13,
        14, 17, 12, 13, 15, 12, 14, 16, 16, 16, 13, 13, 14, 15, 12, 13, 16, 14,
        16, 13, 15, 12, 16, 13, 14, 13, 15, 12, 13, 13, 13, 15, 15, 15, 12, 11,
        15, 11, 15, 14, 15, 15, 12, 16, 15, 13])
prdicted_tokens = tensor([[ 8,  3,  9,  ...,  2,  2,  1],
        [ 3,  9,  6,  ..., 11, 11, 11],
        [ 5,  2, 13,  ...,  6,  1, 11],
        ...,
        [ 8,  3,  5,  ..., 1

Validation epoch 1:   3%|▎         | 103/4114 [00:00<00:16, 250.51it/s]

...

prdicted_tokens = tensor([[ 4,  4, 13,  ...,  1, 11, 11],
        [ 5, 11,  9,  ..., 10,  1, 11],
        [ 9,  5, 13,  ..., 11, 11, 11],
        ...,
        [ 5, 13,  3,  ..., 11, 11, 11],
        [ 9,  4,  6,  ..., 11, 11, 11],
        [ 8,  5,  9,  ...,  4,  6,  1]], device='cuda:0')
batch_y = tensor([[ 0,  0,  0,  ...,  1,  0,  0],
        [ 0,  0,  0,  ..., 10,  1,  0],
        [ 0,  0,  0,  ...,  0,  0,  0],
        ...,
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  4,  6,  1]])
batch_y_lens = tensor([14, 15, 10, 14, 14, 13, 15, 14, 14, 16, 14, 14, 14, 10, 11, 13, 16, 16,
         9, 16, 14, 16, 14, 14, 12, 11, 14, 13, 12, 13, 13, 14, 13, 11, 12, 14,
        12, 12, 13, 12, 15, 14, 13, 12, 14, 11, 11, 12, 11, 11, 14, 14,  9, 15,
        12, 13, 11, 14, 15, 12, 14, 11, 12, 16])
prdicted_tokens = tensor([[ 4,  2,  5,  ..., 11, 11, 11],
        [ 5,  3,  5,  ..., 11, 11, 11],
        [ 4,  6,  5,  ..., 11, 11, 11],
     

Validation epoch 1:  99%|█████████▉| 4072/4114 [00:16<00:00, 250.70it/s]

prdicted_tokens = tensor([[ 5, 10, 13,  ...,  6,  1, 11],
        [ 4,  7, 10,  ...,  1, 11, 11],
        [ 4,  2, 13,  ...,  1, 11, 11],
        ...,
        [ 5, 11,  5,  ..., 11, 11, 11],
        [ 5, 10,  9,  ...,  9,  8,  1],
        [ 3,  3, 13,  ..., 11, 11, 11]], device='cuda:0')
batch_y = tensor([[0, 0, 0,  ..., 6, 1, 0],
        [0, 0, 0,  ..., 1, 0, 0],
        [0, 0, 0,  ..., 1, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 9, 8, 1],
        [0, 0, 0,  ..., 0, 0, 0]])
batch_y_lens = tensor([15, 14, 14, 13, 12, 15, 15, 15, 14, 13, 14, 11, 15, 11, 14, 15, 14, 14,
        15, 15, 13, 15, 12, 16, 16, 16, 12, 13, 11, 14, 14, 11, 16, 16, 15, 14,
        14, 11, 14, 14, 12, 13, 11, 13, 13, 15, 13, 16, 12, 11, 15, 12, 12, 13,
        13, 11, 11, 14, 13, 13, 13, 12, 16, 12])
prdicted_tokens = tensor([[ 8,  5,  4,  ...,  1, 11, 11],
        [ 3, 10, 13,  ...,  1, 11, 11],
        [ 3,  4, 13,  ..., 10,  1, 11],
        ...,
        [ 3, 11, 13,  ..., 1

Validation epoch 1: 100%|██████████| 4114/4114 [00:16<00:00, 247.85it/s]

prdicted_tokens = tensor([[ 8, 13,  3,  ..., 11, 11, 11],
        [ 9,  8,  5,  ..., 11, 11, 11],
        [ 3,  6, 13,  ...,  1, 11, 11],
        ...,
        [ 9,  4,  6,  ...,  8,  1, 11],
        [ 4, 11,  5,  ..., 11, 11, 11],
        [ 3,  5,  6,  ...,  1, 11, 11]], device='cuda:0')
batch_y = tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 1, 0, 0],
        ...,
        [0, 0, 0,  ..., 8, 1, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 1, 0, 0]])
batch_y_lens = tensor([11, 13, 14, 13, 16, 14, 14, 14, 13, 12, 14, 16, 15, 14,  9, 11, 11, 10,
        11, 14, 11, 15, 15, 12, 10, 10, 16, 10, 13, 12, 14, 15, 14, 14, 14, 13,
        15, 13, 13, 15, 13, 13, 14, 14, 12, 11, 11, 14, 14, 15, 16, 13, 15, 16,
        13, 14, 15, 12, 14, 15, 15, 15, 12, 14])
prdicted_tokens = tensor([[ 8,  3, 10,  ...,  1, 11, 11],
        [ 4, 10,  6,  ..., 11, 11, 11],
        [ 3,  5,  6,  ..., 11, 11, 11],
        ...,
        [ 8,  5,  8,  ...,  

# Generation
Use `model.generator` and provide an initial character to automatically generate a sequence.

In [129]:
model = model.to("cpu")
print("".join(model.generator('1+1=')))

TypeError: argmax() got an unexpected keyword argument 'num'